After reading reading in a [tweet](https://twitter.com/LeahNeukirchen/status/1482461732886876163) that you can measure the shockwave of the Hunga Tonga–Hunga Haʻapai erruption using simple air pressure sensors I decided to to check the log of my home automation setup.
Sure enough there was nice little spike about 15h after the erruption.
Since many folks in my electronics bubble on mastodon also run sensors with continous data,
I postet [a screenshot](https://chaos.social/@sebastian/107628740679869429) there.

Sure enough I got quite a few replies of people reporting the time when the wave hit their location.
So I decided to collect some data points and see if we can estimate the propagation speed of the wave,
and maybe find a way to estimate the point of origin from the data.

In [1]:
import sys
!{sys.executable} -m pip install geopy
!{sys.executable} -m pip install ipyleaflet
!{sys.executable} -m pip install tabulate

Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable


In [2]:
from datetime import datetime
from pytz import timezone

data_points = [
    ("Kaiserslautern", datetime(2022, 1, 16, 20, 30, 0, tzinfo=timezone("Europe/Berlin")), "https://chaos.social/@sebastian/107628740679869429"),
    ("Aachen", datetime(2022, 1, 16, 20, 25, 0, tzinfo=timezone("Europe/Berlin")), "https://chaos.social/@trilader/107628784664752716"),
    ("Hamburg", datetime(2022, 1, 16, 20, 10, 0, tzinfo=timezone("Europe/Berlin")),"https://chaos.social/@tsia_/107628923762308800"),
    ("Edinburgh", datetime(2022, 1, 16, 18, 45, 0, tzinfo=timezone("UTC")), "https://toot.cat/@river/107629146900457261"),
    ("Copenhagen", datetime(2022, 1, 16, 19, 55, 0, tzinfo=timezone("CET")), "https://mcd.dk/@rune/107629163090789143"),
    ("Augsburg", datetime(2022, 1, 16, 20, 38, 0, tzinfo=timezone("Europe/Berlin")), "https://chaos.social/@phjl/107629214329242643"),
    ("Frankfurt", datetime(2022, 1, 16, 20, 25, 0, tzinfo=timezone("Europe/Berlin")), "https://mastodon.social/@hko/107629722849924036"),
    ("Melbourne", datetime(2022, 1, 16, 8, 0, 0, tzinfo=timezone("UTC")), "https://aus.social/@futzle/107631253370573653"),
]

Since we know roughly where and when the explosion happened we can do a quick sanity check of our data points.

In [3]:
from geopy.distance import distance
from geopy.geocoders import Nominatim

geolocator = Nominatim(user_agent="pressure_wave_triangulation")

ORIGIN = (-20.5, -175.4)
T_ZERO = datetime(2022, 1, 16, 4, 27, 0, tzinfo=timezone("UTC"))

SPEED_OF_SOUND = 343.0 # Speed of sound in air at 20°C

enhanced_data_points = []

for location, ts, url in data_points:
    geolocation = geolocator.geocode(location)
    coordinates = (geolocation.latitude, geolocation.longitude)
    dist = distance(ORIGIN, coordinates)
    
    delta_t = ts - T_ZERO
    
    speed = dist.meters / delta_t.total_seconds()
    mach = speed / SPEED_OF_SOUND

    enhanced_data_points += [(location, coordinates, ts, dist, delta_t, speed, mach, url)]


In [4]:
import tabulate

table_data = [("Location", "Coordinates", "Timestamp", "Distance", "Time difference", "Speed [m/s]", "Mach Number", "Toot")]
for location, coordinates, ts, dist, delta_t, speed, mach, url in enhanced_data_points:
    table_data += [(location, "%f %f" % coordinates, ts, dist, delta_t, speed, mach, url)]

table = tabulate.tabulate(table_data, tablefmt='html')
table


'<table>\n<tbody>\n<tr><td>Location      </td><td>Coordinates          </td><td>Timestamp                </td><td>Distance             </td><td>Time difference</td><td>Speed [m/s]       </td><td>Mach Number       </td><td>Toot                                              </td></tr>\n<tr><td>Kaiserslautern</td><td>49.443217 7.768995   </td><td>2022-01-16 20:30:00+00:53</td><td>16780.572549711476 km</td><td>15:10:00       </td><td>307.3364935844593 </td><td>0.8960247626369076</td><td>https://chaos.social/@sebastian/107628740679869429</td></tr>\n<tr><td>Aachen        </td><td>50.776351 6.083862   </td><td>2022-01-16 20:25:00+00:53</td><td>16641.951165318445 km</td><td>15:05:00       </td><td>306.4816052544834 </td><td>0.8935323768352286</td><td>https://chaos.social/@trilader/107628784664752716 </td></tr>\n<tr><td>Hamburg       </td><td>53.550341 10.000654  </td><td>2022-01-16 20:10:00+00:53</td><td>16307.144415681687 km</td><td>14:50:00       </td><td>305.3772362487207 </td><td>0.8903126421245501</td><td>https://chaos.social/@tsia_/107628923762308800    </td></tr>\n<tr><td>Edinburgh     </td><td>55.953346 -3.188375  </td><td>2022-01-16 18:45:00+00:00</td><td>16015.614674425336 km</td><td>14:18:00       </td><td>311.1036261543383 </td><td>0.9070076564266423</td><td>https://toot.cat/@river/107629146900457261        </td></tr>\n<tr><td>Copenhagen    </td><td>55.686724 12.570072  </td><td>2022-01-16 19:55:00+01:00</td><td>16042.101561186751 km</td><td>14:28:00       </td><td>308.02806377086694</td><td>0.8980410022474254</td><td>https://mcd.dk/@rune/107629163090789143           </td></tr>\n<tr><td>Augsburg      </td><td>48.366804 10.898697  </td><td>2022-01-16 20:38:00+00:53</td><td>16861.97644995329 km </td><td>15:18:00       </td><td>306.13610112478744</td><td>0.8925250761655611</td><td>https://chaos.social/@phjl/107629214329242643     </td></tr>\n<tr><td>Frankfurt     </td><td>50.110644 8.682092   </td><td>2022-01-16 20:25:00+00:53</td><td>16699.02015177992 km </td><td>15:05:00       </td><td>307.53259948029324</td><td>0.8965964999425459</td><td>https://mastodon.social/@hko/107629722849924036   </td></tr>\n<tr><td>Melbourne     </td><td>-37.814218 144.963161</td><td>2022-01-16 08:00:00+00:00</td><td>4264.645211600706 km </td><td>3:33:00        </td><td>333.6968084194606 </td><td>0.9728769924765615</td><td>https://aus.social/@futzle/107631253370573653     </td></tr>\n</tbody>\n</table>'

That looks quite consistent, considering the we pretty much guestimated the timestamps from screenshots.
On the other hand it's easy mode because we know the time and point of origin for the wave.

Let's see if we can estimate the propagation speed using the relative delay between the diffrent locations:

In [21]:
relative_speed_data = []

for location, coordinates, ts, _, _, _, _, url in enhanced_data_points:
    count = 0
    speed = 0.0
    for _, other_coordinates, other_ts, _, _, _, _, _ in enhanced_data_points:
        relative_delay = other_ts - ts
        if abs(relative_delay.total_seconds()) < 1:
            continue
        
        relative_dist = distance(coordinates, other_coordinates)
        relative_speed = relative_dist.meters / abs(relative_delay.total_seconds())
        
        if relative_speed > 343:
            continue
        
        speed += relative_speed
        count += 1.0
        
        
    if count < 1.0:
        continue 
        
    speed = speed / count
    print(location, speed)
    
    relative_speed_data += [(location, coordinates, ts, speed)]
    
        

Kaiserslautern 322.0800766318187
Aachen 306.3924371618201
Hamburg 219.6723878081226
Edinburgh 315.16138946596874
Copenhagen 283.03327184485505
Augsburg 298.8056038343784
Frankfurt 319.0927106279109


Some cleanup was required, so I ended up dropping everthing that is faster then the speed of sound in air.
I don't think a pressure wave can be supersonic. At least not for long.

Unfortunately the leaftlet map does something weird here. 
It seems to disagree with the distances calculated by geopy.
If we cicle each of our locations with the distance we got from geopy, the circles never really intersect.

In [25]:
from ipyleaflet import Map, Marker, Circle


MELBOURNE = geolocator.geocode("Melbourne")


leaflet_map = Map(center=(MELBOURNE.latitude, MELBOURNE.longitude), zoom=2)
marker = Marker(location=ORIGIN, draggable=False)
leaflet_map.add_layer(marker);

for _, coordinates, _, dist, _, _, _, _ in enhanced_data_points:
    marker = Marker(location=coordinates, draggable=False)
    leaflet_map.add_layer(marker);
    
    circle = Circle(location=coordinates, radius=int(dist.meters), fill=False, weight=1)
    leaflet_map.add_layer(circle)


display(leaflet_map)


Map(center=[-37.8142176, 144.9631608], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_tit…

However we can fiddle with that so that things end up in roughly the right spot. (Highly scientific. I know...)

In [26]:
from ipyleaflet import Map, Marker, Circle


FUDGE_FACTOR = 0.821


leaflet_map = Map(center=(MELBOURNE.latitude, MELBOURNE.longitude), zoom=2)
marker = Marker(location=ORIGIN, draggable=False)
leaflet_map.add_layer(marker);

for _, coordinates, _, dist, _, _, _, _ in enhanced_data_points:
    marker = Marker(location=coordinates, draggable=False)
    leaflet_map.add_layer(marker);
    
    circle = Circle(location=coordinates, radius=int(dist.meters * FUDGE_FACTOR), fill=False, weight=1)
    leaflet_map.add_layer(circle)


display(leaflet_map)

Map(center=[-37.8142176, 144.9631608], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_tit…

Also I don't want to mess with the math required to actually propagate back the circles projected on a sphere until they actually intersec.

So let's just assume we have a rough idea when the event occured and we can use that timestamp +-5min to draw some circles and use our eyes to check for intersections.

In [27]:
from ipyleaflet import Map, Marker, Circle


leaflet_map = Map(center=ORIGIN, zoom=2)
marker = Marker(location=ORIGIN, draggable=False)
leaflet_map.add_layer(marker);


T_MINUS = datetime(2022, 1, 16, 4, 22, 0, tzinfo=timezone("UTC"))
T_PLUS = datetime(2022, 1, 16, 4, 32, 0, tzinfo=timezone("UTC"))


for location, coordinates, ts, speed in relative_speed_data:
    marker = Marker(location=coordinates, draggable=False)
    leaflet_map.add_layer(marker);
    
    for start, color in [(T_MINUS, "green"), (T_ZERO, "red"), (T_PLUS, "blue")]:
        dist = speed * (ts - start).total_seconds()

        circle = Circle(location=coordinates, radius=int(dist * FUDGE_FACTOR), fill=False, weight=1, color=color)
        leaflet_map.add_layer(circle)


display(leaflet_map)

Map(center=[-20.5, -175.4], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

While that looks close, just zoom out until you can see the entire map.

It's a mess.
Not enough data points, the locations are not spread out wide enough, the timestamps are off, and there is some weird map projection stuff going on....